In [384]:
files_year = 2012

In [385]:
hijri_months = r"(Muharram|Safar|Rabi[‘’']?\s?al-awwal|Rabi[‘’']?\s?al-thani|Jumada\s?al-awwal|Jumada\s?al-thani|Rajab|Chaâbane|Sha‘ban|Ramadan|Shawwal|Dhou\s?El\s?Kaada|Dhou\s?El\s?Hidja|Dhu\s?al-Qi‘dah|Dhu\s?al-Hijjah)"

In [386]:
import os
import json

In [387]:
data_file_path = f'./files/{str(files_year)}/data.json'

In [388]:
import json
import os

def read_json_file():
    if not os.path.exists(data_file_path):
        return []
    with open(data_file_path, 'r') as f:
        return json.load(f)


all_data = read_json_file()

In [389]:
import json
import pandas as pd
import datefinder

import string

result = []

In [390]:
def extract_data(all_data):
    for content in all_data:

        file = content['content']
        file = file[1: ]

        # get metadata
        metadata = file[1].split('\n')
        
        hijri_date = metadata[0].split('JOURNAL')[0]
        gregorian_date = metadata[1].split('JOURNAL')[0]

        source_match = re.search(r"N°\s*(\d+)", file[1])
        source = source_match.group(1) if source_match else 0

        # start extracting content
        data = {}
        data['metadata'] = {
            "journal_number": source,
            "hijri_date": hijri_date,
            "gregorian_date": gregorian_date
        }
        data['types'] = []

        df = pd.DataFrame(file)


        sommaire = df[0][0].split('\n')
        sommaire = pd.DataFrame(sommaire)

        titles = [col for col in sommaire[0] if col.isupper()]
        titles = [col for col in titles if not any(char.isdigit() for char in col)]
        titles = [col for col in titles if "OFFICIELLE" or 'JOURNAL' not in col]
        if titles:

            titles = titles[1: ]
    
            for i, title in enumerate(titles):
                if title != '' and not title.startswith('MINISTERE'):
                    data['types'].append({
                        'type_name': title,
                        'ministries': []
                    })
                elif title != '' and data['types'][-1] and title.startswith('MINISTERE'):
                    data['types'][-1]['ministries'].append({
                        'ministry_name': title,
                        'decrets': []
                    })
            
            for data_type in data['types']: 
                if data_type['ministries'] == []:
                    data_type['ministries'].append({
                        'ministry_name': '',
                        'decrets': []
                    })
            
            df = df[~df[0].str.contains('SOMMAIRE', case=False, na=False)]
    
            file = ' '.join(file)

            current_type = None
            decret_pattern = re.compile(r"^(?:Décret exécutif n°\s*\d+.*|Décision n°\s*\d+.*|Loi n°\s*\d+.*|Décret présidentiel du\s*\d+.*|Décret présidentiel n°\s*\d+.*|Arrêté du\s*\d+.*|Arrêtés du\s*\d+.*|Arrêté interministériel du\s*\d+.*)$", re.IGNORECASE | re.MULTILINE)
            article_pattern = re.compile(r"^(?:Article|Art\.)\s+\d*|l\.", re.IGNORECASE | re.MULTILINE)
            citation_pattern = re.compile(r"^Vu\s+.*$", re.IGNORECASE | re.MULTILINE)
    
            current_decret = ''
            current_articles = []
            current_citations = []
            others = ''
    
            for index, row in df.iterrows():
                content = row[0].strip().split('\n\n')
                for text in content:
                    text = text.replace('\n', ' ')
                    text = text.strip().strip(string.punctuation)
                    if text == '' or 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in text or 'Décrète :' == text or 'Arrête :' == text or 'Sur le rapport' in text or "Le Président de la République" in text or 'x' == text:
                        continue

                    for entry in data["types"]:
                        if text == entry["type_name"]:
                            current_type = entry  
                            break
                
                    if current_type and text not in [t["type_name"] for t in data["types"]]:
                        
                        for min_entry in current_type["ministries"]:
                            if min_entry["ministry_name"] and min_entry["ministry_name"].lower() in text.lower():
                                ministry = min_entry
                                current_decret = ''
                                break
                            else:
                                ministry = current_type["ministries"][0]
                        
                        if decret_pattern.match(text):
                            if current_decret:
                                for structure in ministry["decrets"]:
                                    if structure["decret_title"] == current_decret:
                                        structure["articles"] = current_articles
                                        structure["citations"] = current_citations
                                        structure["others"] = others
                                        break
                    
                            current_decret = text
                            current_articles = []
                            current_citations = []
                            others = ''
                        
                        elif article_pattern.match(text):
                            words = text.strip().split()
                            if words[0] in ['Article', 'Art.']:
                                number = words[1].replace("er.", "").replace(".", "").replace("—", "").replace("&", "")
                                words = words[2:]
                                words = ' '.join(words)
                            current_articles.append({
                                "article_title": 'Article ' + number,
                                "article_content": words
                            })
                    
                        elif current_articles:
                            current_articles[-1]["article_content"] += " " + text
                    
                        elif citation_pattern.match(text):
                            current_citations.append(text)
                        else:
                            others += text
                
                        if not ministry["decrets"] or not any(dec['decret_title'] == current_decret for dec in ministry["decrets"]):
                            ministry["decrets"].append({
                                'decret_title': current_decret,
                                "articles": current_articles,
                                "citations": current_citations,
                                'others': others
                            })
            result.append(data)


import pandas as pd
import re
result = []

extract_data(all_data)

In [391]:
print(json.dumps(result, indent=4, ensure_ascii=False))

[
    {
        "metadata": {
            "journal_number": "01",
            "hijri_date": "20 Safar 1433 ",
            "gregorian_date": ""
        },
        "types": [
            {
                "type_name": "‘ DECISIONS INDIVIDUELLES",
                "ministries": [
                    {
                        "ministry_name": "",
                        "decrets": [
                            {
                                "decret_title": "Décret présidentiel du 18 Moharram 1433 correspondant au 13 décembre 2011 mettant fin aux fonctions d’une sous-directrice à la direction générale des archives natiOnalEs ………….…….….…..….…..……rreureearenmenentenserenceneareneerenrenenreneenensanenrenennenrenenseneenen cec en cec",
                                "articles": [],
                                "citations": [],
                                "others": ""
                            },
                            {
                                "decret_title": "Décret p

In [392]:
with open(f'./files/{str(files_year)}/result.json', 'w') as f:
    json.dump(result, f)